<a href="https://colab.research.google.com/github/VieiraJardel/Data_Science/blob/main/Covid_HeatMap.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#HeatMap CIDADES COVID-19

Heatmap (mapa de calor) é uma técnica de visualização de dados que mostra a magnitude de um fenômeno como cor em duas dimensões. A variação na cor pode ser por matiz ou intensidade, fornecendo pistas visuais óbvias sobre como o fenômeno está agrupado ou varia ao longo do espaço. Aqui iremos criar um mapa de calor em python para visualizar a intensidade dos casos de COVID-19 em cada cidade do Brasil onde foram registrados casos.

In [ ]:
#Importar bibliotecas
import pandas as pd
import numpy as np

In [ ]:
#Importando o Folium - O Folium trabalha é uma biblioteca que trabalha com camadas de mapas
!pip install folium
import folium
from folium import plugins

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
#Conectar ao Drive para ter acesso a arquivos 
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


A base de dados utilizada foi importada do **Brasil.IO**

O Brasil.IO tem como objetivo facilitar o acesso a dados públicos brasileiros. O projeto é desenvolvido de forma colaborativa, todo o código está disponível como software livre e os custos são pagos através de uma campanha de financiamento coletivo.

Essa tabela possui os casos confirmados e óbitos obtidos dos boletins das Secretarias Estaduais de Saúde. Dados capturados em 27 de Março de 2022. Importação dos dados feita em 27 de Março de 2022 às 20:28:29.

In [ ]:
#Importar base de dados
df = pd.read_csv("/content/gdrive/MyDrive/Colab Notebooks/03 - Projeto COVID-19/caso.csv")

#Verificando dimensoes
print("Dimensoes do dataset",
      "\nVariáveis: ",df.shape[1], 
      "\nEntradas: ", df.shape[0])

#Ver entradas
df.head()

Dimensoes do dataset 
Variáveis:  13 
Entradas:  2838003


date state city place_type  confirmed  deaths  order_for_place  \
0  2022-03-27    AP  NaN      state     160328    2122              734   
1  2022-03-26    AP  NaN      state     160321    2122              733   
2  2022-03-25    AP  NaN      state     160314    2122              732   
3  2022-03-24    AP  NaN      state     160301    2122              731   
4  2022-03-23    AP  NaN      state     160288    2122              730   

   is_last  estimated_population_2019  estimated_population  city_ibge_code  \
0     True                   845731.0              861773.0            16.0   
1    False                   845731.0              861773.0            16.0   
2    False                   845731.0              861773.0            16.0   
3    False                   845731.0              861773.0            16.0   
4    False                   845731.0              861773.0            16.0   

   confirmed_per_100k_inhabitants  death_rate  
0                     18604.43527      0.0132  
1                     18603.62300      0.0132  
2                     18602.81072      0.0132  
3                     18601.30220      0.0132  
4                     18599.79368      0.0132

In [ ]:
#Ver saídas
df.tail()

date state  city place_type  confirmed  deaths  \
2837998  2020-06-23    SP  Óleo       city          1       0   
2837999  2020-06-22    SP  Óleo       city          1       0   
2838000  2020-06-21    SP  Óleo       city          1       0   
2838001  2020-06-20    SP  Óleo       city          1       0   
2838002  2020-06-19    SP  Óleo       city          1       0   

         order_for_place  is_last  estimated_population_2019  \
2837998                5    False                     2496.0   
2837999                4    False                     2496.0   
2838000                3    False                     2496.0   
2838001                2    False                     2496.0   
2838002                1    False                     2496.0   

         estimated_population  city_ibge_code  confirmed_per_100k_inhabitants  \
2837998                2471.0       3533809.0                        40.46945   
2837999                2471.0       3533809.0                        40.46945   
2838000                2471.0       3533809.0                        40.46945   
2838001                2471.0       3533809.0                        40.46945   
2838002                2471.0       3533809.0                        40.46945   

         death_rate  
2837998         0.0  
2837999         0.0  
2838000         0.0  
2838001         0.0  
2838002         0.0

##Extrair código de IBGE para encontrar Latitude e Longitude

Para o mapa de calor precisamos da latitude e logitude de cada cidade e estado.

O arquivo cidades_brasil.csv contem o código do IBGE de todas as cidades do Brasil e informações de latitude e longitude

Como o arquivo do Brasil IO possui uma coluna que possui o código de cada cidade (city_ibge_code) podemos juntar as bases de dados

In [ ]:
#Novo dataframe com dados do IBGE
cidades = pd.read_csv("/content/gdrive/MyDrive/Colab Notebooks/03 - Projeto COVID-19/cidades_brasil.csv")

cidades.head()

codigo_ibge                 nome  latitude  longitude  capital  codigo_uf
0      5200050      Abadia de Goiás -16.75730   -49.4412        0         52
1      3100104  Abadia dos Dourados -18.48310   -47.3916        0         31
2      5200100            Abadiânia -16.19700   -48.7057        0         52
3      3100203               Abaeté -19.15510   -45.4444        0         31
4      1500107           Abaetetuba  -1.72183   -48.8788        0         15

In [ ]:
#Alterar o Index do dataset, deixar que código seja o index
cidades = cidades.set_index("codigo_ibge")

cidades.head()

nome  latitude  longitude  capital  codigo_uf
codigo_ibge                                                              
5200050          Abadia de Goiás -16.75730   -49.4412        0         52
3100104      Abadia dos Dourados -18.48310   -47.3916        0         31
5200100                Abadiânia -16.19700   -48.7057        0         52
3100203                   Abaeté -19.15510   -45.4444        0         31
1500107               Abaetetuba  -1.72183   -48.8788        0         15

##Data Processing - Pré processamento de dados

Na base de dados do Brasil.IO a coluna *place_type* possui cidades e estados. Vamos fazer um novo dataframe selecionando apenas as cidades, isso removerá quase 20 mil linhas. 

In [ ]:
#Novo dataframe com apenas cidades em 'place_type'
cities = df.loc[df.place_type == "city", :] 

#Conferir se selecionou apenas cidades
cities.place_type.unique()

array(['city'], dtype=object)

In [ ]:
#Verificando dimensoes
print("Dimensoes do dataset",
      "\nVariáveis: ",cities.shape[1], 
      "\nEntradas: ", cities.shape[0])

#Ver entradas
cities.head()

Dimensoes do dataset 
Variáveis:  13 
Entradas:  2818241


date state   city place_type  confirmed  deaths  order_for_place  \
734  2021-12-14    AP  Amapá       city       1424      13              586   
735  2021-12-13    AP  Amapá       city       1424      13              585   
736  2021-12-12    AP  Amapá       city       1424      13              584   
737  2021-12-11    AP  Amapá       city       1424      13              583   
738  2021-12-10    AP  Amapá       city       1424      13              582   

     is_last  estimated_population_2019  estimated_population  city_ibge_code  \
734     True                     9109.0                9187.0       1600105.0   
735    False                     9109.0                9187.0       1600105.0   
736    False                     9109.0                9187.0       1600105.0   
737    False                     9109.0                9187.0       1600105.0   
738    False                     9109.0                9187.0       1600105.0   

     confirmed_per_100k_inhabitants  death_rate  
734                     15500.16327      0.0091  
735                     15500.16327      0.0091  
736                     15500.16327      0.0091  
737                     15500.16327      0.0091  
738                     15500.16327      0.0091

##Juntar base de dados
Unir dataframe do Brasil IO com dados do arquivo csv do IBGE através do index com código de cada cidade 

In [ ]:
#Unir latitude e longitude por código do IBGE
cities = cities.join(cidades, on="city_ibge_code")

#Ver como ficaram as entradas
cities.head()

date state   city place_type  confirmed  deaths  order_for_place  \
734  2021-12-14    AP  Amapá       city       1424      13              586   
735  2021-12-13    AP  Amapá       city       1424      13              585   
736  2021-12-12    AP  Amapá       city       1424      13              584   
737  2021-12-11    AP  Amapá       city       1424      13              583   
738  2021-12-10    AP  Amapá       city       1424      13              582   

     is_last  estimated_population_2019  estimated_population  city_ibge_code  \
734     True                     9109.0                9187.0       1600105.0   
735    False                     9109.0                9187.0       1600105.0   
736    False                     9109.0                9187.0       1600105.0   
737    False                     9109.0                9187.0       1600105.0   
738    False                     9109.0                9187.0       1600105.0   

     confirmed_per_100k_inhabitants  death_rate   nome  latitude  longitude  \
734                     15500.16327      0.0091  Amapá   2.05267   -50.7957   
735                     15500.16327      0.0091  Amapá   2.05267   -50.7957   
736                     15500.16327      0.0091  Amapá   2.05267   -50.7957   
737                     15500.16327      0.0091  Amapá   2.05267   -50.7957   
738                     15500.16327      0.0091  Amapá   2.05267   -50.7957   

     capital  codigo_uf  
734      0.0       16.0  
735      0.0       16.0  
736      0.0       16.0  
737      0.0       16.0  
738      0.0       16.0

In [ ]:
cities.shape

(2818241, 18)

Vamos selecionar apenas algumas colunas do DataFrame. Nao são necessários todos os dados.

Iremos buscar o ultimo número de casos de cada cidade, para isso recorreremos a coluna *is_last*.

In [ ]:
#novo dataframe com campo "is_last" = True
geo_last = cities.loc[cities.is_last==True , ["city", "latitude", "longitude", "state", "confirmed", "deaths"]]

geo_last

city   latitude  longitude state  confirmed  deaths
734                   Amapá   2.052670   -50.7957    AP       1424      13
1320               Calçoene   2.504750   -50.9512    AP       1852      14
1901                 Cutias   0.970761   -50.8005    AP        874       7
2478         Ferreira Gomes   0.857256   -51.1795    AP       1566       7
3058                Itaubal   0.602185   -50.6996    AP        550       3
...                     ...        ...        ...   ...        ...     ...
2835558  Águas de São Pedro -22.597700   -47.8734    SP        461      12
2836080    Álvares Florence -20.320300   -49.9141    SP        626      16
2836553     Álvares Machado -22.076400   -51.4722    SP       2507      79
2837057  Álvaro de Carvalho -22.084100   -49.7190    SP        292       9
2837551                Óleo -22.943500   -49.3419    SP        156       5

[5589 rows x 6 columns]

In [ ]:
#contar número de cidades acometidas por covid 19
len(geo_last)

5589

In [ ]:
#Somar quantidade de casos
geo_last.confirmed.sum()

23550890

In [ ]:
#Somar quantidade de mortes
geo_last.deaths.sum()

615373

In [ ]:
#Mostar estados por valor unico
geo_last.state.unique()

array(['AP', 'AC', 'AM', 'AL', 'DF', 'ES', 'CE', 'BA', 'MS', 'MA', 'GO',
       'MT', 'PA', 'PE', 'PB', 'PI', 'RJ', 'MG', 'RN', 'RR', 'RO', 'PR',
       'SE', 'SC', 'TO', 'RS', 'SP'], dtype=object)

In [ ]:
#Contar estados afetados
len(geo_last.state.unique())

27

Para o mapa de calor é necessário passar latitude, longitude e o valor de casos confirmados

In [ ]:
#Novo dataframe com colunas para o mapa
coordenadas = geo_last[["latitude", "longitude", "confirmed"]]

coordenadas

latitude  longitude  confirmed
734       2.052670   -50.7957       1424
1320      2.504750   -50.9512       1852
1901      0.970761   -50.8005        874
2478      0.857256   -51.1795       1566
3058      0.602185   -50.6996        550
...            ...        ...        ...
2835558 -22.597700   -47.8734        461
2836080 -20.320300   -49.9141        626
2836553 -22.076400   -51.4722       2507
2837057 -22.084100   -49.7190        292
2837551 -22.943500   -49.3419        156

[5589 rows x 3 columns]

In [ ]:
#Remover linhas com NaN
coordenadas = coordenadas.dropna()

coordenadas

latitude  longitude  confirmed
734       2.052670   -50.7957       1424
1320      2.504750   -50.9512       1852
1901      0.970761   -50.8005        874
2478      0.857256   -51.1795       1566
3058      0.602185   -50.6996        550
...            ...        ...        ...
2835558 -22.597700   -47.8734        461
2836080 -20.320300   -49.9141        626
2836553 -22.076400   -51.4722       2507
2837057 -22.084100   -49.7190        292
2837551 -22.943500   -49.3419        156

[5570 rows x 3 columns]

#Criando Mapa

Largura e altura em 100% para quando salvamos em html ele ocupar a tela inteira. Em location colocamos as coordenados do Brasil

In [ ]:
#Criar mapa
baseMap = folium.Map(
                width="100%",
                height="100%",
                location=[-15.788497, -47.879873],
                zoom_start=4
)

In [ ]:
baseMap

#Desenhar mapa de calor sobre o mapa

In [ ]:
#Adicionar camada 
baseMap = baseMap.add_child(plugins.HeatMap(coordenadas))

In [ ]:
baseMap

In [ ]:
#Salvar mapa
baseMap.save("01MapacalorCovid-19.html")

#Identificar cidade com casos e mortes por circulo em cada cidade

Vamos incrementar ao mapa pontos identificando a cidade com casos confirmados e mortes. Vamos fazer isso atraves do inserimento de circulos nas cidades com o tamanho proporcional a quantidade de casos confirmados.

O primeiro passo é remover as linhas que constam NaN, assim como fizemos com o DF coordenadas.

In [ ]:
#Remover NaN
geo_last = geo_last.dropna()
geo_last

city   latitude  longitude state  confirmed  deaths
734                   Amapá   2.052670   -50.7957    AP       1424      13
1320               Calçoene   2.504750   -50.9512    AP       1852      14
1901                 Cutias   0.970761   -50.8005    AP        874       7
2478         Ferreira Gomes   0.857256   -51.1795    AP       1566       7
3058                Itaubal   0.602185   -50.6996    AP        550       3
...                     ...        ...        ...   ...        ...     ...
2835558  Águas de São Pedro -22.597700   -47.8734    SP        461      12
2836080    Álvares Florence -20.320300   -49.9141    SP        626      16
2836553     Álvares Machado -22.076400   -51.4722    SP       2507      79
2837057  Álvaro de Carvalho -22.084100   -49.7190    SP        292       9
2837551                Óleo -22.943500   -49.3419    SP        156       5

[5570 rows x 6 columns]

In [ ]:
geo_last.iloc[0]["latitude"]

2.05267

A cor #00FF6A (tom de verde forte) foi selecionada devido ser complementar ao vermelho que predomina o HeatMap. Quando temos cores complementares conseguimos fazer com que o contraste seja absoluto, conseguimos fazer o verde se dastacar ao coloca-lo sobre o vermelho.

In [ ]:
#Plotar circulo em cidade
for i in range(0,len(geo_last)):
    folium.Circle(
        location = [geo_last.iloc[i]["latitude"] , geo_last.iloc[i]["longitude"]],
        color   = "#00FF6A",
        fill    = "#00A1B3",
        tooltip = "<li><bold> CIDADE: " + str(geo_last.iloc[i]["city"]) +       "</bold></li>" +
                  "<li><bold> ESTADO: " + str(geo_last.iloc[i]["state"]) +      "</bold></li>" +
                  "<li><bold> CASOS: " + str(geo_last.iloc[i]["confirmed"]) +   "</bold></li>" +
                  "<li><bold> MORTES: " + str(geo_last.iloc[i]["deaths"]) +     "</bold></li>",   
        radius  = (geo_last.iloc[i]["confirmed"]**0.8)
    ).add_to(baseMap)

In [ ]:
baseMap

In [ ]:
#Salvar mapa
baseMap.save("02MapacalorCovid-19.html")